# Xception and Pretraining Procedure for Crowd Counting

In this notebook we propose a solution for Crowd Counting problem evaluated on Mall Dataset. Here we use pretraining on Shanghai Tech Dataset according to method mentioned in the paper. As the starting point, we use Xception model pretrained on Imagenet Dataset.

In order to find suitable values for number of unfrozen layers, we use optuna framework. In general, we test 2 approaches:

1. **Xception**

  We use Xception model with small fully connected regression block with dropout layers and ReLU activations.

2.   **Xception + Data Augmentation**

  In this section, we also exploit horizontal flip augmentation.
  
For all approaches, we search optimal number of unfrozen layers both for pretraining and training phases. This is done by applying Optuna framework.

Lastly, we use two loss function: MSE and MAPE. While working with ShanghaiTech dataset, MSE gives a huge penalty to overcrowded pictures which leads to overfitting. In order to overcome this problem, we switch to MAPE after validation MAE stops improving. Also we perform this procedure during training phase because it appeared to improve results.

In [1]:
import os
import re

import pytorch_lightning as pl
import torch
import torchvision
from torchvision import datasets, transforms
from torchvision.transforms import Pad
from torchvision.models import resnet50, ResNet50_Weights
from torch import nn
from torch.nn import functional as F
from torch.optim.lr_scheduler import ReduceLROnPlateau
from torch.utils.data import DataLoader, random_split

import pandas as pd
import numpy as np

from torchvision.utils import make_grid
from torch.utils.data import Dataset, DataLoader
import torchmetrics
from PIL import Image

import timm
from timm.layers import create_classifier

from sklearn.model_selection import train_test_split
import optuna
from copy import deepcopy
import requests
import shutil
import scipy.io
import kaggle

from matplotlib import pyplot as plt
%matplotlib inline

In [2]:
# Training params
BATCH_SIZE = 32
PRETRAINING_NUM_EPOCHS = 30
TRAINING_NUM_EPOCHS = 50
N_ITER = 10
PRETRAIN_TEST_SIZE = 0.01
TRAINVAL_SIZE = 0.8
RANDOM_STATE = 42

# Paths
DATA_PATH = '../data'
MALL_DATA_PATH = '../data/Mall'
SHAN_DATA_PATH = '../data/ShanghaiTech'
MODEL_PATH = '../models'

In [3]:
class CustomDataset(Dataset):

    def __init__(self, annotations, root_dir, transform=None):

        self.annotations = annotations
        self.root_dir = root_dir
        self.transform = transform

    def __len__(self):
        return len(self.annotations)

    def __getitem__(self, idx):
        if torch.is_tensor(idx):
            idx = idx.tolist()

        img_info = self.annotations.iloc[idx]
        img_name = img_info['image_name']
        counts = img_info['count']

        image = Image.open(img_name).convert(mode='RGB')
        image = self.transform(image)
        counts = torch.tensor(counts, dtype=torch.float32)
        sample = (image, counts)
        return sample

In [4]:
class DataModule(pl.LightningDataModule):

    def __init__(self, trainval_annotations, test_annotations,
                 root_dir, train_transform=None, val_transform=None,
                 test_transform=None):
        super().__init__()

        self.trainval_annotations = trainval_annotations
        self.test_annotations = test_annotations
        self.root_dir = root_dir
        self.train_transform = train_transform
        self.val_transform = val_transform
        self.test_transform = test_transform

    def prepare_data(self):
        pass

    def setup(self, stage: str):

        if stage == "fit" or stage is None:
            train_set_full = CustomDataset(self.trainval_annotations, 
                                           self.root_dir,
                                           self.train_transform)
            generator = torch.Generator().manual_seed(RANDOM_STATE)
            self.train, self.validate = random_split(train_set_full, 
                                                     [round(len(train_set_full) * TRAINVAL_SIZE), 
                                                      len(train_set_full) - 
                                                      round(len(train_set_full) * TRAINVAL_SIZE)], 
                                                     generator=generator)

            self.validate.transform = self.val_transform
        if stage == "test" or stage is None:
            self.test = CustomDataset(self.test_annotations, 
                                      self.root_dir,
                                      self.test_transform)

    def train_dataloader(self):
        return DataLoader(self.train, batch_size=BATCH_SIZE)

    def val_dataloader(self):
        return DataLoader(self.validate, batch_size=BATCH_SIZE)

    def test_dataloader(self):
        return DataLoader(self.test, batch_size=BATCH_SIZE)

In [5]:
class XceptionBase(pl.LightningModule):

    def __init__(self,
                 lr=0.001,
                 loss='mse',
                 sch_factor=0.2,
                 sch_patience=3,
                 sch_min_lr=1e-6,
                 sch_monitor='val_mse',
                 **kwargs):
        super().__init__()

        self.lr = lr
        self.loss = loss
        self.num_features = 2048
        self.loss_dict = {'mse': nn.MSELoss,
                          'mape': torchmetrics.MeanAbsolutePercentageError}

        self.model = timm.create_model('xception', features_only=True,
                                       pretrained=True)

        for param in self.model.parameters():
            param.requires_grad = False

        self.global_pool, _ = create_classifier(self.num_features, 1,
                                                pool_type='avg')

        self.fc_block = None

        self.define_loss(self.loss)
        self.define_scheduller(sch_factor,
                               sch_patience,
                               sch_min_lr,
                               sch_monitor)

        self.train_mse = torchmetrics.MeanSquaredError()
        self.val_mse = torchmetrics.MeanSquaredError()
        self.test_mse = torchmetrics.MeanSquaredError()

        self.train_mae = torchmetrics.MeanAbsoluteError()
        self.val_mae = torchmetrics.MeanAbsoluteError()
        self.test_mae = torchmetrics.MeanAbsoluteError()

        self.train_mape = torchmetrics.MeanAbsolutePercentageError()
        self.val_mape = torchmetrics.MeanAbsolutePercentageError()
        self.test_mape = torchmetrics.MeanAbsolutePercentageError()

    def unfreeze_n_layers(self, n_unfreeze):
        self.counter = 0
        self.n_unfreeze = n_unfreeze
        self._recursive_step(self.model)

    def _recursive_step(self, block):
        if self.counter == self.n_unfreeze:
            return
        children = list(block.children())[::-1]
        parameters = list(block.parameters())
        if children:
            for child in children:
                self._recursive_step(child)
                if self.counter == self.n_unfreeze:
                    return
        elif parameters:
            for param in block.parameters():
                param.requires_grad = True
            self.counter += 1

        if self.counter == self.n_unfreeze:
            return

    def forward(self, x):
        x = self.model(x)[-1]
        x = self.global_pool(x)
        preds = self.fc_block(x)
        return preds

    def define_loss(self, loss_name):
        self.loss_fn = self.loss_dict[loss_name]()

    def define_scheduller(self, sch_factor=0.2,
                          sch_patience=3,
                          sch_min_lr=1e-6,
                          sch_monitor='val_mse'):

        self.sch_factor = sch_factor
        self.sch_patience = sch_patience
        self.sch_min_lr = sch_min_lr
        self.sch_monitor = sch_monitor


    def training_step(self, batch, batch_idx):

        x, y = batch
        y = y.view(-1, 1)

        preds = self.forward(x)

        loss = self.loss_fn(preds, y)
        self.train_mse(preds, y.view(-1, 1))
        self.train_mae(preds, y.view(-1, 1))
        self.train_mape(preds, y.view(-1, 1))

        self.log('train_mse', self.train_mse, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)
        self.log('train_mae', self.train_mae, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)
        self.log('train_mape', self.train_mape, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)

        cur_lr = self.trainer.optimizers[0].param_groups[0]['lr']
        self.log("lr", cur_lr, prog_bar=True, on_epoch=True)

        return loss

    def validation_step(self, batch, batch_idx):

        x,y = batch
        y = y.view(-1, 1)

        preds = self.forward(x)
        loss = self.loss_fn(preds, y)

        self.val_mse(preds, y.view(-1, 1))
        self.val_mae(preds, y.view(-1, 1))
        self.val_mape(preds, y.view(-1, 1))

        self.log('val_mse', self.val_mse, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)
        self.log('val_mae', self.val_mae, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)
        self.log('val_mape', self.val_mape, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)


    def test_step(self, batch, batch_idx):

        x,y = batch
        y = y.view(-1, 1)
        preds = self.forward(x)

        self.test_mse(preds, y.view(-1, 1))
        self.test_mae(preds, y.view(-1, 1))
        self.test_mape(preds, y.view(-1, 1))

        self.log('test_mse', self.test_mse, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)
        self.log('test_mae', self.test_mae, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)
        self.log('test_mape', self.test_mape, 
                 on_epoch=True, prog_bar=True, 
                 logger=True)

    def configure_optimizers(self):

        optimizer = torch.optim.Adam(self.parameters(), lr=self.lr)
        return {"optimizer": optimizer,
                "lr_scheduler": {"scheduler": ReduceLROnPlateau(optimizer, 
                                                                factor=self.sch_factor,
                                                                patience=self.sch_patience,
                                                                min_lr=self.sch_min_lr),
                "monitor": self.sch_monitor}}

In [6]:
class Xception(XceptionBase):

    def __init__(self,
                 lr=0.001,
                 loss='mse',
                 sch_factor=0.2,
                 sch_patience=3,
                 sch_min_lr=1e-6,
                 sch_monitor='val_mse',
                 **kwargs):
        super().__init__(lr,
                         loss,
                         sch_factor,
                         sch_patience,
                         sch_min_lr,
                         sch_monitor)

        self.fc_block = nn.Sequential(
            nn.Linear(2048, 400),
            nn.ReLU(),
            nn.Dropout(0.2),
            nn.Linear(400, 400),
            nn.ReLU(),
            nn.Dropout(0.2),
            nn.Linear(400, 400),
            nn.ReLU(),
            nn.Dropout(0.2),
            nn.Linear(400, 1)
        )

In [7]:
class MetricsCallback(pl.callbacks.Callback):
    """Recording all metrics"""

    def __init__(self):
        super().__init__()
        self.metrics = []

    def on_validation_epoch_end(self, trainer, pl_module):
        each_me = deepcopy(trainer.callback_metrics)
        self.metrics.append(each_me)

In [8]:
def train(model, pretrain_n_unfreeze, train_n_unfreeze):
    '''
    Training procedure
    '''
    
    global PRETRAINING_NUM_EPOCHS, TRAINING_NUM_EPOCHS, shan_datamodule, mall_datamodule
    
    callbacks_st1 = [pl.callbacks.EarlyStopping(monitor='val_mse', mode='min', patience=5),
                     pl.callbacks.LearningRateMonitor(logging_interval='epoch')]

    callbacks_st2 = [pl.callbacks.EarlyStopping(monitor='val_mae', mode='min', patience=5),
                     pl.callbacks.LearningRateMonitor(logging_interval='epoch')]

    callbacks_st3 = [pl.callbacks.EarlyStopping(monitor='val_mse', mode='min', patience=5),
                     pl.callbacks.LearningRateMonitor(logging_interval='epoch')]
    
    callbacks_st4 = [pl.callbacks.EarlyStopping(monitor='val_mae', mode='min', patience=5),
                     pl.callbacks.LearningRateMonitor(logging_interval='epoch')]

    # stage 1: pretraining with MSE
    model.unfreeze_n_layers(pretrain_n_unfreeze)

    trainer = pl.Trainer(max_epochs=PRETRAINING_NUM_EPOCHS, callbacks=callbacks_st1)
    trainer.fit(model, shan_datamodule)

    # stage 2: pretraining with MAPE
    model.define_loss('mape')
    model.define_scheduller(sch_factor=0.2,
                                 sch_patience=3,
                                 sch_min_lr=1e-6,
                                 sch_monitor='val_mae')

    trainer = pl.Trainer(max_epochs=PRETRAINING_NUM_EPOCHS, callbacks=callbacks_st2)
    trainer.fit(model, shan_datamodule)

    # stage 3: training with MSE
    model.define_loss('mse')
    model.define_scheduller(sch_factor=0.2,
                                 sch_patience=3,
                                 sch_min_lr=1e-6,
                                 sch_monitor='val_mse')
    model.unfreeze_n_layers(train_n_unfreeze)

    trainer = pl.Trainer(max_epochs=TRAINING_NUM_EPOCHS,
                         callbacks=callbacks_st3)
    trainer.fit(model, mall_datamodule)
    
    # stage 4: training with MAPE
    model.define_loss('mape')
    model.define_scheduller(sch_factor=0.2,
                                 sch_patience=3,
                                 sch_min_lr=1e-6,
                                 sch_monitor='val_mae')

    trainer = pl.Trainer(max_epochs=TRAINING_NUM_EPOCHS, 
                         callbacks=callbacks_st4)
    trainer.fit(model, mall_datamodule)  
    return trainer, model

In [9]:
def objective(trial):
    '''
    Function to optimize number
    of unfrozen layers
    '''

    global model_class, model_name, best_mae, best_model
    
    pretrain_n_unfreeze = trial.suggest_int("pretrain_n_unfreeze", 10, 39)
    train_n_unfreeze = trial.suggest_int("train_n_unfreeze", pretrain_n_unfreeze, 40)

    curr_model = model_class(loss='mse')
    trainer, curr_model = train(curr_model, pretrain_n_unfreeze, train_n_unfreeze)

    val_metrics = trainer.validate(curr_model, mall_datamodule)
    val_mae = val_metrics[0]['val_mae']
    
    if val_mae < best_mae:
        best_mae = val_mae
        best_model = deepcopy(curr_model)
        trainer.save_checkpoint(os.path.join(MODEL_PATH, 
                                             '{}.ckpt'.format(model_name)).\
                                             replace("\\","/"))
        
    return val_mae

## Download the data

Mall data

In [102]:
!kaggle datasets download -d fmena14/crowd-counting


  0%|          | 0.00/1.18G [00:00<?, ?B/s]
  0%|          | 1.00M/1.18G [00:00<12:26, 1.69MB/s]
  0%|          | 2.00M/1.18G [00:00<06:23, 3.29MB/s]
  0%|          | 3.00M/1.18G [00:00<04:49, 4.35MB/s]
  0%|          | 5.00M/1.18G [00:01<02:59, 7.02MB/s]
  1%|          | 7.00M/1.18G [00:01<02:32, 8.24MB/s]
  1%|          | 8.00M/1.18G [00:01<02:24, 8.67MB/s]
  1%|          | 9.00M/1.18G [00:01<02:19, 9.02MB/s]
  1%|          | 10.0M/1.18G [00:01<02:15, 9.28MB/s]
  1%|          | 12.0M/1.18G [00:01<02:07, 9.78MB/s]
  1%|1         | 13.0M/1.18G [00:01<02:06, 9.91MB/s]
  1%|1         | 14.0M/1.18G [00:01<02:04, 10.0MB/s]
  1%|1         | 16.0M/1.18G [00:02<02:02, 10.2MB/s]
  1%|1         | 17.0M/1.18G [00:02<02:01, 10.2MB/s]
  1%|1         | 18.0M/1.18G [00:02<02:06, 9.86MB/s]
  2%|1         | 20.0M/1.18G [00:02<01:58, 10.5MB/s]
  2%|1         | 21.0M/1.18G [00:02<01:59, 10.4MB/s]
  2%|1         | 22.0M/1.18G [00:02<01:59, 10.4MB/s]
  2%|1         | 24.0M/1.18G [00:02<01:58, 10.5MB/s]
 

In [103]:
zip_path = 'crowd-counting.zip'
destination_path = '../data1/mall_dataset'

# Extract the contents of the zip file
shutil.unpack_archive(zip_path, MALL_DATA_PATH)

# Clean up: remove the downloaded zip file
os.remove(zip_path)

ShanghaiTech Data

In [107]:
!kaggle datasets download -d tthien/shanghaitech-with-people-density-map


  0%|          | 0.00/4.79G [00:00<?, ?B/s]
  0%|          | 1.00M/4.79G [00:00<50:19, 1.70MB/s]
  0%|          | 2.00M/4.79G [00:00<25:52, 3.31MB/s]
  0%|          | 3.00M/4.79G [00:00<20:16, 4.22MB/s]
  0%|          | 5.00M/4.79G [00:01<12:38, 6.77MB/s]
  0%|          | 6.00M/4.79G [00:01<11:26, 7.48MB/s]
  0%|          | 7.00M/4.79G [00:01<10:32, 8.12MB/s]
  0%|          | 8.00M/4.79G [00:01<09:55, 8.61MB/s]
  0%|          | 9.00M/4.79G [00:01<09:30, 8.99MB/s]
  0%|          | 10.0M/4.79G [00:01<09:11, 9.29MB/s]
  0%|          | 11.0M/4.79G [00:01<08:58, 9.53MB/s]
  0%|          | 12.0M/4.79G [00:01<08:48, 9.70MB/s]
  0%|          | 13.0M/4.79G [00:01<08:41, 9.83MB/s]
  0%|          | 14.0M/4.79G [00:01<08:51, 9.64MB/s]
  0%|          | 15.0M/4.79G [00:02<08:45, 9.75MB/s]
  0%|          | 16.0M/4.79G [00:02<08:38, 9.88MB/s]
  0%|          | 17.0M/4.79G [00:02<08:34, 9.95MB/s]
  0%|          | 18.0M/4.79G [00:02<08:30, 10.0MB/s]
  0%|          | 19.0M/4.79G [00:02<08:31, 10.0MB/s]
 

In [108]:
zip_path = 'shanghaitech-with-people-density-map.zip'

# Extract the contents of the zip file
shutil.unpack_archive(zip_path, DATA_PATH)

# Clean up: remove the downloaded zip file
os.remove(zip_path)

## Read the data

Mall data

In [10]:
# read ground truth data

mall_df = pd.read_csv(os.path.join(MALL_DATA_PATH, 'labels.csv').\
                      replace("\\","/"))
mall_df['image_name'] = mall_df['id'].apply(lambda x: '{}/frames/frames/seq_{:06d}.jpg'.\
                                            format(MALL_DATA_PATH, x))

In [11]:
trainval_mall_df, test_mall_df = train_test_split(
    mall_df,
    train_size=TRAINVAL_SIZE,
    random_state=RANDOM_STATE,
)

ShanghaiTech data

In [12]:
shan_info = []

for dir_1 in os.listdir(SHAN_DATA_PATH):
    for dir_2 in os.listdir(os.path.join(SHAN_DATA_PATH, dir_1).\
                            replace("\\","/")):
        files_lst = os.listdir(os.path.join(SHAN_DATA_PATH, dir_1, dir_2, 'images').\
                               replace("\\","/"))
        gt_list = os.listdir(os.path.join(SHAN_DATA_PATH, dir_1, dir_2, 'ground-truth').\
                             replace("\\","/"))
        
        for i, gt in enumerate(gt_list):
            img_name = files_lst[i]
            mat = scipy.io.loadmat(os.path.join(SHAN_DATA_PATH, dir_1, dir_2, 
                                                'ground-truth', gt).replace("\\","/"))
            count_ = mat['image_info'][0][0][0][0][1][0][0]
            shan_info.append({'id': i, 'count': count_, 
                          'image_name': os.path.join(SHAN_DATA_PATH, dir_1, dir_2, 
                                                     'images', img_name).replace("\\","/")})
            
shan_df = pd.DataFrame(shan_info)

In [13]:
trainval_shan_df, test_shan_df = train_test_split(
    shan_df,
    test_size=PRETRAIN_TEST_SIZE,
    random_state=RANDOM_STATE
)

## Xception

In [14]:
train_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225])
])

val_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225])
])

test_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225])
])


mall_datamodule = DataModule(trainval_mall_df, test_mall_df,
                             MALL_DATA_PATH, train_transform,
                             val_transform, test_transform)
shan_datamodule = DataModule(trainval_shan_df,
                             test_shan_df,
                             SHAN_DATA_PATH, train_transform,
                             val_transform, test_transform)

In [ ]:
model_class = Xception
model_name = 'xception'
best_mae = np.inf
best_model = None

current_study = optuna.create_study()
current_study.optimize(objective, n_trials=N_ITER)

[I 2024-02-06 22:19:16,986] A new study created in memory with name: no-name-3a40706e-4c2e-4f5a-be51-c2322478a670
C:\Users\Max\anaconda3\lib\site-packages\timm\models\_factory.py:117: UserWarning: Mapping deprecated model name xception to current legacy_xception.
  model = create_fn(
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

   | Name        | Type                        | Params
-------------------------------------------------------------
0  | model       | FeatureHookNet              | 20.8 M
1  | global_pool | SelectAdaptivePool2d        | 0     
2  | loss_fn     | MSELoss                     | 0     
3  | train_mse   | MeanSquaredError            | 0     
4  | val_mse     | MeanSquaredError            | 0     
5  | test_mse    | MeanSquaredError            | 0     
6  | train_mae   | MeanAbsoluteError           | 0     
7  | val_m

Sanity Checking: |                                       | 0/? [00:00<?, ?it/s]

C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'val_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'train_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\loops\fit_loop.py:293: The number of training batches (30) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.


Training: |                                              | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

...

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

In [16]:
current_study.best_params

{'pretrain_n_unfreeze': 14, 'train_n_unfreeze': 38}

In [19]:
trainer = pl.Trainer()
xception_best = deepcopy(best_model)
trainer.validate(xception_best, mall_datamodule)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'val_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Validation: |                                            | 0/? [00:00<?, ?it/s]

────────────────────────────────────────────────────────────────────────────────
     Validate metric           DataLoader 0
────────────────────────────────────────────────────────────────────────────────
         val_mae            1.8336471319198608
        val_mape            0.0594826266169548
         val_mse             5.425953388214111
────────────────────────────────────────────────────────────────────────────────


[{'val_mse': 5.425953388214111,
  'val_mae': 1.8336471319198608,
  'val_mape': 0.0594826266169548}]

In [20]:
trainer.test(xception_best, mall_datamodule)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'test_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Testing: |                                               | 0/? [00:00<?, ?it/s]

────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────
        test_mae            1.7154728174209595
        test_mape           0.05480390042066574
        test_mse             4.946479320526123
────────────────────────────────────────────────────────────────────────────────


[{'test_mse': 4.946479320526123,
  'test_mae': 1.7154728174209595,
  'test_mape': 0.05480390042066574}]

In [15]:
#best_model = Xception.load_from_checkpoint('../models/xception.ckpt')

C:\Users\Max\anaconda3\lib\site-packages\timm\models\_factory.py:117: UserWarning: Mapping deprecated model name xception to current legacy_xception.
  model = create_fn(


## Xception + Data Augmentation

In [14]:
train_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225],
                        ),
    transforms.RandomHorizontalFlip()
])

val_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225])
])

test_transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize([0.485, 0.456, 0.406],
                             [0.229, 0.224, 0.225])
])


mall_datamodule = DataModule(trainval_mall_df, test_mall_df,
                             MALL_DATA_PATH, train_transform,
                             val_transform, test_transform)
shan_datamodule = DataModule(trainval_shan_df,
                             test_shan_df,
                             SHAN_DATA_PATH, train_transform,
                             val_transform, test_transform)

In [ ]:
model_class = Xception
model_name = 'xception_aug'
best_mae = np.inf
best_model = None

current_study = optuna.create_study()
current_study.optimize(objective, n_trials=N_ITER)

[I 2024-02-07 01:44:30,669] A new study created in memory with name: no-name-5ebcb97d-51d6-49e9-8708-82e14a5d103b
C:\Users\Max\anaconda3\lib\site-packages\timm\models\_factory.py:117: UserWarning: Mapping deprecated model name xception to current legacy_xception.
  model = create_fn(
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

   | Name        | Type                        | Params
-------------------------------------------------------------
0  | model       | FeatureHookNet              | 20.8 M
1  | global_pool | SelectAdaptivePool2d        | 0     
2  | loss_fn     | MSELoss                     | 0     
3  | train_mse   | MeanSquaredError            | 0     
4  | val_mse     | MeanSquaredError            | 0     
5  | test_mse    | MeanSquaredError            | 0     
6  | train_mae   | MeanAbsoluteError           | 0     
7  | val_m

Sanity Checking: |                                       | 0/? [00:00<?, ?it/s]

C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'val_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'train_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\loops\fit_loop.py:293: The number of training batches (30) is smaller than the logging interval Trainer(log_every_n_steps=50). Set a lower value for log_every_n_steps if you want to see logs for the training epoch.


Training: |                                              | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

...

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

Validation: |                                            | 0/? [00:00<?, ?it/s]

In [23]:
current_study.best_params

{'pretrain_n_unfreeze': 12, 'train_n_unfreeze': 37}

In [21]:
trainer = pl.Trainer()
xception_aug_best = deepcopy(best_model)
trainer.validate(xception_aug_best, mall_datamodule)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'val_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Validation: |                                            | 0/? [00:00<?, ?it/s]

────────────────────────────────────────────────────────────────────────────────
     Validate metric           DataLoader 0
────────────────────────────────────────────────────────────────────────────────
         val_mae            1.8290491104125977
        val_mape            0.05981369689106941
         val_mse             5.596611022949219
────────────────────────────────────────────────────────────────────────────────


[{'val_mse': 5.596611022949219,
  'val_mae': 1.8290491104125977,
  'val_mape': 0.05981369689106941}]

In [22]:
trainer.test(xception_aug_best, mall_datamodule)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
C:\Users\Max\anaconda3\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:441: The 'test_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=7` in the `DataLoader` to improve performance.


Testing: |                                               | 0/? [00:00<?, ?it/s]

────────────────────────────────────────────────────────────────────────────────
       Test metric             DataLoader 0
────────────────────────────────────────────────────────────────────────────────
        test_mae             1.664007306098938
        test_mape           0.05365889146924019
        test_mse             4.764477729797363
────────────────────────────────────────────────────────────────────────────────


[{'test_mse': 4.764477729797363,
  'test_mae': 1.664007306098938,
  'test_mape': 0.05365889146924019}]

In [19]:
#best_model =  Xception.load_from_checkpoint('../models/xception_aug.ckpt')
#mall_datamodule.setup('fit')